In [0]:
from google.colab import drive
drive.mount('/content/gdrive', force_remount=True)


Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
!mkdir Dataset_224

In [0]:
cd Dataset_224/

/content/Dataset_224


In [0]:
!unzip "/content/gdrive/My Drive/eva-04/S15A/Dataset_224.zip"

In [0]:
cd /content

/content



#MODEL SUMMARY

In [0]:
from torchsummary import summary
from __future__ import print_function
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torchvision import datasets, transforms
import models as models
import os
from models import DenseDepthDNN2 as m
import importlib
importlib.reload(m)
model = m.DenseDepthDNN2().cuda()
summary(model, (6,256,256))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Conv2d-1         [-1, 64, 256, 256]           3,520
              ReLU-2         [-1, 64, 256, 256]               0
       BatchNorm2d-3         [-1, 64, 256, 256]             128
            Conv2d-4         [-1, 64, 256, 256]          36,928
              ReLU-5         [-1, 64, 256, 256]               0
       BatchNorm2d-6         [-1, 64, 256, 256]             128
         MaxPool2d-7        [-1, 128, 128, 128]               0
            Conv2d-8        [-1, 128, 128, 128]         147,584
              ReLU-9        [-1, 128, 128, 128]               0
      BatchNorm2d-10        [-1, 128, 128, 128]             256
           Conv2d-11        [-1, 128, 128, 128]         295,040
             ReLU-12        [-1, 128, 128, 128]               0
      BatchNorm2d-13        [-1, 128, 128, 128]             256
           Conv2d-14        [-1, 128, 1

/usr/local/lib/python3.6/dist-packages/torch/nn/functional.py:1569: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


#Create Data Loaders

In [0]:
#import custom_transforms
# Data loading code
import torch
import torchvision.transforms
#/content/gdrive/My Drive/eva-04/S15A/datasets/MonacularDepthDataset.py

import cdataset.MonacularDepthDataset as dt
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")

normalize = transforms.Normalize(mean=[149.17579724, 143.51813416, 136.34473418],
                                        std=[10.918, 10.54722837, 9.7497292])
#train_transform = custom_transforms.Compose([
#    custom_transforms.RandomHorizontalFlip(),
#    custom_transforms.RandomScaleCrop(),
#    custom_transforms.ArrayToTensor(),
#    normalize
#])

train_transform = transforms.Compose([
        transforms.ToTensor()]) 

#args.data = "/content/gdrive/My Drive/eva-04/S15A/Dataset_224/perfect_128_dw70_sum_30k_lre5_5"
#print("=> fetching scenes in '{}'".format(args.data))

train_set = dt.MonacularDepth_Dataset('/content/Dataset_224/', size = 300000, transform = train_transform)

train_loader = torch.utils.data.DataLoader(train_set, batch_size=16,
                                          shuffle=True, num_workers=1,pin_memory=False)

#valid_transform = transforms.Compose([transforms.ToTensor()])
#test_set = dt.MonacularDepthEstimation_Dataset('/content/Dataset_224/', size = 100000, test=True, transform = valid_transform)

#val_loader = torch.utils.data.DataLoader(test_set, batch_size=1, shuffle=False, num_workers=1,pin_memory=True)


In [0]:
!pwd

/content


In [0]:
pip install pytorch-msssim

In [0]:
pip install kmeans-pytorch

In [0]:
!cp "/content/gdrive/My Drive/eva-04/dense32_depth_mask_128.pth"  /content/dense_depth_mask_256.pth

#Train the Modal

In [0]:
import importlib
import torch
import torch.nn.functional as F
from tqdm import tqdm
from pytorch_msssim import MS_SSIM, ms_ssim, SSIM, ssim
epoch_size = 1
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
optim_params = [{'params': model.parameters(), 'lr': 1e-4}]

#optimizer = torch.optim.Adam(optim_params, lr = 1e-4,weight_decay=0)
#optimizer = torch.optim.SGD(optim_params, lr=2e-4, momentum=0.9, weight_decay=1e-4)
optimizer = torch.optim.SGD(optim_params, lr=1e-4, momentum=0.9, weight_decay=0)
#scheduler = torch.optim.lr_scheduler.CyclicLR(optimizer, 1e-4, 0.1, step_size_up=1000, step_size_down=None, mode='triangular', gamma=1.0, scale_fn=None, scale_mode='cycle', cycle_momentum=True, base_momentum=0.8, max_momentum=0.9, last_epoch=-1)

import logging
logging.basicConfig(filename = "/content/dense_mask_loss_256.log",datefmt='%H:%M:%S',level=logging.DEBUG)

epochs = 1
w = torch.load("/content/dense_depth_mask_256.pth")    
model.load_state_dict(w)
import timeit
import torch     
import train

for epoch in range(epochs):
    correct = 0
    processed = 0

    pbar = tqdm(train_loader)
    preds = np.zeros((16, 1,18750,256), dtype=np.float32)
    labels = np.zeros((16,1,18750,256),dtype=np.float32)
    last_batch = 18750
    train.train(model, train_loader, optimizer, epoch, preds, labels,last_batch)


  0%|          | 0/18750 [00:00<?, ?it/s]/usr/local/lib/python3.6/dist-packages/torch/nn/functional.py:1569: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:143: RuntimeWarning: invalid value encountered in true_divide
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:148: RuntimeWarning: divide by zero encountered in log10
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:148: RuntimeWarning: invalid value encountered in subtract
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:151: RuntimeWarning: invalid value encountered in true_divide
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:152: RuntimeWarning: invalid value encountered in less
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:155: RuntimeWarning: invalid value encountered in less
/usr/local/lib/

#Test the Modal and display the output comparison

In [0]:
modal.eval()
test_loss = 0
correct = 0
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
from PIL import Image
import cv2
from google.colab.patches import cv2_imshow
#import cv2_utils
from torchvision import transforms
count = 0
w = torch.load("/content/dense_depth_mask_256.pth")
#w = torch.load("/content/verygood_128_dw70_sum_100k_lre5_10.pth")
modal.load_state_dict(w)
import random
import time      
im_array = []
bg_array = []
fgbg_array = []
depth_array = []
mask_array =[]
om_array =[]
od_array =[]
#gstart = 1
#gstart = 300723
gstart1 = random.randint(300200, 399990)
gstart = random.randint(gstart1, 399990)
gstart = 1

print("random test seed=",gstart)
valid_transform = transforms.Compose([transforms.ToTensor()])

test_set1 = BackgroundSubtraction_Dataset('/content/Dataset_224/', size = 100000, test=True, start = gstart,transform = valid_transform)
val_loader = torch.utils.data.DataLoader(test_set1, batch_size=1,
                                         shuffle=False, num_workers=1,pin_memory=False)

with torch.no_grad(): 
  #preds = np.zeros((1,1,2350,64), dtype=np.float32)
  #labels = np.zeros((1,1,2350,64),dtype=np.float32)
    
  for input_array1 in val_loader:
      count = count + 1
      #print(input_array1[0])
      bg = input_array1[0].to(device)
      fgbg = input_array1[1].to(device)
      depth_img = input_array1[2].to(device)
      mask_img = input_array1[3].to(device)

      concat = torch.cat([bg,fgbg],dim=1)
      output = modal(concat)
      
      bg = bg.cpu()
      fgbg = fgbg.cpu()
      
      img = output[0].cpu()
      #img = F.interpolate(img, size=(128, 128),mode='bilinear',align_corners=False)
      mask = output[1].cpu()

      depth_array.append(img)
      mask_array.append(mask)

      bg_array.append(bg)
      fgbg_array.append(fgbg)

      od = input_array1[2].cpu()
      om = input_array1[3].cpu()
      
      od_array.append(od)
      om_array.append(om)


      #pred = pred.cpu().numpy()
      label = depth_img.cpu()
      depth_img = depth_img.cpu() 
      
      if count == 10:
        print('file=',input_array1[4])
        print('file=',input_array1[5])
        print('file=',input_array1[6])
        print('file=',input_array1[7])
        break
      #cv2.imwrite("/content/prediction/img1.jpg",img)
      
import matplotlib.pyplot as plt
from mpl_toolkits.axes_grid1 import ImageGrid
import numpy as np

trans = transforms.ToPILImage(mode=None)
        
for im in bg_array:
  im_array.append(trans(im.squeeze()))

for im in fgbg_array:
  im_array.append(trans(im.squeeze()))

for im in od_array:
  im_array.append(trans(im.squeeze()))

for im in om_array:
  im_array.append(trans(im.squeeze()).convert('LA'))

for im in depth_array:
  #im = 0.2 + im.squeeze()
  im_array.append(trans(im.squeeze()))

for im in mask_array:
  im_array.append(trans(im.squeeze()).convert('LA'))

fig = plt.figure(figsize=(256,256))
grid = ImageGrid(fig, 111,  # similar to subplot(111)
                 nrows_ncols=(6, 10),  # creates 2x2 grid of axes
                 axes_pad=0.1,  # pad between axes in inch.
                 )
fig.set_label(str(gstart))
for ax, im in zip(grid, im_array):
    # Iterating over the grid returns the Axes..
    ax.imshow(im)

plt.show()

random test seed= 1


/usr/local/lib/python3.6/dist-packages/torch/nn/functional.py:1569: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


file= ('/content/Dataset_224/bg/bg1.jpg',)
file= ('/content/Dataset_224/bg1/fg_1/overlay/10.jpg',)
file= ('/content/Dataset_224/bg1/fg_1/depth/10.jpg',)
file= ('/content/Dataset_224/bg1/fg_1/mask/10.jpg',)


#Loss Functions

In [0]:
from kmeans_pytorch import kmeans
# data
#data_size, dims, num_clusters = 1000, 2, 3
#x = np.random.randn(data_size, dims) / 6
#x = torch.from_numpy(x)

# kmeans
#cluster_ids_x, cluster_centers = kmeans(
#    X=x, num_clusters=num_clusters, distance='euclidean', device=torch.device('cuda:0')
#)

def gradient_loss(gen_frames, gt_frames, alpha=1):

    def gradient(x):
        # idea from tf.image.image_gradients(image)
        # https://github.com/tensorflow/tensorflow/blob/r2.1/tensorflow/python/ops/image_ops_impl.py#L3441-L3512
        # x: (b,c,h,w), float32 or float64
        # dx, dy: (b,c,h,w)

        h_x = x.size()[-2]
        w_x = x.size()[-1]
        # gradient step=1
        left = x
        right = F.pad(x, [0, 1, 0, 0])[:, :, :, 1:]
        top = x
        bottom = F.pad(x, [0, 0, 0, 1])[:, :, 1:, :]

        # dx, dy = torch.abs(right - left), torch.abs(bottom - top)
        dx, dy = right - left, bottom - top 
        # dx will always have zeros in the last column, right-left
        # dy will always have zeros in the last row,    bottom-top
        dx[:, :, :, -1] = 0
        dy[:, :, -1, :] = 0

        return dx, dy

    # gradient
    gen_dx, gen_dy = gradient(gen_frames)
    gt_dx, gt_dy = gradient(gt_frames)
    #
    grad_diff_x = torch.abs(gt_dx - gen_dx)
    grad_diff_y = torch.abs(gt_dy - gen_dy)

    # condense into one tensor and avg
    return torch.mean(grad_diff_x ** alpha + grad_diff_y ** alpha)

#with sobel filters
def gradient_loss_function_using_sobel(x):
  a = torch.Tensor([[1, 0, -1],
  [2, 0, -2],
  [1, 0, -1]])

  a = a.view((1,1,3,3))
  G_x = F.conv2d(x, a)

  b = torch.Tensor([[1, 2, 1],
  [0, 0, 0],
  [-1, -2, -1]])

  b = b.view((1,1,3,3))
  G_y = F.conv2d(x, b)

  G = torch.sqrt(torch.pow(G_x,2)+ torch.pow(G_y,2))
  return G

def gradient(x):
      # idea from tf.image.image_gradients(image)
      # https://github.com/tensorflow/tensorflow/blob/r2.1/tensorflow/python/ops/image_ops_impl.py#L3441-L3512
      # x: (b,c,h,w), float32 or float64
      # dx, dy: (b,c,h,w)

      h_x = x.size()[-2]
      w_x = x.size()[-1]
      # gradient step=1
      left = x
      right = F.pad(x, [0, 1, 0, 0])[:, :, :, 1:]
      top = x
      bottom = F.pad(x, [0, 0, 0, 1])[:, :, 1:, :]

      # dx, dy = torch.abs(right - left), torch.abs(bottom - top)
      dx, dy = right - left, bottom - top 
      # dx will always have zeros in the last column, right-left
      # dy will always have zeros in the last row,    bottom-top
      dx[:, :, :, -1] = 0
      dy[:, :, -1, :] = 0

      return dx, dy
from pytorch_msssim import MS_SSIM, ms_ssim, SSIM, ssim
from kmeans_pytorch import kmeans, kmeans_predict

def depth_loss_function(y_true, y_pred, theta=0.1, maxDepthVal=1000.0/10.0):
    
    #Point-wise depth
    data_size, dims, num_clusters = 1024, 2, 6
    
    #l_depth = K.mean(K.abs(y_pred - y_true), axis=-1)

    ldepth_ids_x, cluster_centers = kmeans(X=torch.abs(y_pred - y_true), num_clusters=6, distance='euclidean', device=torch.device('cuda:0'))


    # Edges
    #dy_true, dx_true = tf.image.image_gradients(y_true)
    dx_true,dy_true = gradient(y_true)
    #dy_pred, dx_pred = tf.image.image_gradients(y_pred)
    dx_pred,dy_pred = gradient(y_pred)

    #l_edges = kmeans(K.abs(dy_pred - dy_true) + K.abs(dx_pred - dx_true), axis=-1)
    l_edges_y, cluster_centers_y = kmeans(Y=(torch.abs(dy_pred - dy_true) + torch.abs(dx_pred - dx_true)),num_clusters=6)

    # Structural similarity (SSIM) index
    l_ssim = torch.clamp((1 - ssim(y_true, y_pred, maxDepthVal)) * 0.5, 0, 1)

    # Weights
    w1 = 1.0
    w2 = 1.0
    w3 = theta

    ldepth = kmeans_predict(ldepth_ids_x,cluster_centers)
    ledges = kmeans_predict(l_edges_y,cluster_centers_y)

    #return (w1 * l_ssim) + (w2 * kmean(l_edges)) + (w3 * K.mean(l_depth))
    return (w1 * l_ssim) + (w2 * l_edges) + (w3 * l_depth)

def smooth_loss(pred_map):
    def gradient(pred):
        D_dy = pred[:, :, 1:] - pred[:, :, :-1]
        D_dx = pred[:, :, :, 1:] - pred[:, :, :, :-1]
        return D_dx, D_dy

    if type(pred_map) not in [tuple, list]:
        pred_map = [pred_map]

    loss = 0
    weight = 1.

    for scaled_map in pred_map:
        dx, dy = gradient(scaled_map)
        dx2, dxdy = gradient(dx)
        dydx, dy2 = gradient(dy)
        loss += (dx2.abs().mean() + dxdy.abs().mean() + dydx.abs().mean() + dy2.abs().mean())*weight
        weight /= 2.3  # don't ask me why it works better
    return loss
